# df009_FromScratchVSTTree
Compare creation of a ROOT dataset with RDataFrame and TTree.

This tutorial illustrates how much simpler it can be to use a
RDataFrame to create a dataset with respect to the usage
of the TTree interfaces.




**Author:** Danilo Piparo (CERN)  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Monday, December 22, 2025 at 04:16 AM.</small></i>

 ##This is the classic way of creating a ROOT dataset
The steps are:
- Create a file
- Create a tree associated to the file
- Define the variables to write in the entries
- Define the branches associated to those variables
- Write the event loop to set the right value to the variables
- Call TTree::Fill to save the value of the variables
- Write the TTree
- Close the file
 

In [1]:
%%cpp -d
void classicWay()
{
   TFile f("df009_FromScratchVSTTree_classic.root", "RECREATE");
   TTree t("treeName", "treeName");
   double b1;
   int b2;
   t.Branch("b1", &b1);
   t.Branch("b2", &b2);
   for (int i = 0; i < 10; ++i) {
      b1 = i;
      b2 = i * i;
      t.Fill();
   }
   t.Write();
   f.Close();
}

 ##This is the RDF way of creating a ROOT dataset
Few lines are needed to achieve the same result.
Parallel creation of the TTree is not supported in the
classic method.
In this case the steps are:
- Create an empty RDataFrame
- If needed, define variables for the functions used to fill the branches
- Create new columns expressing their content with lambdas, functors, functions or strings
- Invoke the Snapshot action


Parallelism is not the only advantage. Starting from an existing dataset,
filtering it, enriching it with new columns, leaving aside some other columns, and
writing a new dataset become very easy to do.
 

In [2]:
%%cpp -d
void RDFWay()
{
   ROOT::RDataFrame df(10);
   auto b = 0.;
   df.Define("b1", [&b]() { return b++; })
     .Define("b2", "(int) b1 * b1")  This can even be a string
     .Snapshot("treeName", "df009_FromScratchVSTTree_df.root");
}

input_line_49:6:36: error: expected ';' after expression
     .Define("b2", "(int) b1 * b1")  This can even be a string
                                   ^
                                   ;
input_line_49:6:38: error: unknown type name 'This'
     .Define("b2", "(int) b1 * b1")  This can even be a string
                                     ^
input_line_49:6:46: error: expected ';' at end of declaration
     .Define("b2", "(int) b1 * b1")  This can even be a string
                                             ^
                                             ;


In [3]:
classicWay();
RDFWay();

In module 'ROOTDataFrame':
/github/home/ROOT-CI/build/include/ROOT/RDF/RDefine.hxx:110:4: error: function 'ROOT::Detail::RDF::RDefine<(lambda), ROOT::Detail::RDF::ExtraArgsForDefine::None>::RDefine' is used but not defined in this translation unit, and cannot be defined in any other translation unit because its type does not have linkage
   RDefine(std::string_view name, std::string_view type, F expression, const ROOT::RDF::ColumnNames_t &columns,
   ^
/usr/lib/gcc/x86_64-redhat-linux/11/../../../../include/c++/11/ext/new_allocator.h:162:23: note: used here
        { ::new((void *)__p) _Up(std::forward<_Args>(__args)...); }
                             ^
In module 'ROOTDataFrame':
/github/home/ROOT-CI/build/include/ROOT/RDF/RDefine.hxx:121:4: warning: function 'ROOT::Detail::RDF::RDefine<(lambda), ROOT::Detail::RDF::ExtraArgsForDefine::None>::~RDefine' has internal linkage but is not defined [-Wundefined-internal]
   ~RDefine() { fLoopManager->Deregister(this); }
   ^
/github/home/ROOT